In [ ]:
!source /content/venv/bin/python3.11
!pip install -qU unsloth
!pip install -qU huggingface_hub hf_transfer

/bin/bash: line 1: /content/venv/bin/python3.11: No such file or directory


In [3]:
import os
from huggingface_hub import snapshot_download

os.environ["HF_HUB_ENABLE_HF_TRANSFER"] = "1"
snapshot_download(
    repo_id = "unsloth/gemma-3n-E4B-it-GGUF",
    local_dir = "unsloth/gemma-3n-E4B-it-GGUF",
    allow_patterns=["*UD-Q4_K_XL*","mmproj-BF16.gguf"]
)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


Fetching 1 files:   0%|          | 0/1 [00:00<?, ?it/s]

gemma-3n-E4B-it-UD-Q4_K_XL.gguf:   0%|          | 0.00/5.39G [00:00<?, ?B/s]

'/content/unsloth/gemma-3n-E4B-it-GGUF'

In [41]:
from unsloth import FastModel
import torch

model_name = "unsloth/gemma-3n-E4B-it"
model, tokenizer = FastModel.from_pretrained(
    model_name = model_name,
    dtype = torch.bfloat16,
    max_seq_length = 1024,
    load_in_4bit = True
)

==((====))==  Unsloth 2025.7.8: Fast Gemma3N patching. Transformers: 4.53.2.
   \\   /|    Tesla T4. Num GPUs = 1. Max memory: 14.741 GB. Platform: Linux.
O^O/ \_/ \    Torch: 2.7.1+cu126. CUDA: 7.5. CUDA Toolkit: 12.6. Triton: 3.3.1
\        /    Bfloat16 = FALSE. FA [Xformers = 0.0.31.post1. FA2 = False]
 "-____-"     Free license: http://github.com/unslothai/unsloth
Unsloth: Fast downloading is enabled - ignore downloading bars which are red colored!
Unsloth: Gemma3N does not support SDPA - switching to eager!


model.safetensors.index.json: 0.00B [00:00, ?B/s]

Fetching 3 files:   0%|          | 0/3 [00:00<?, ?it/s]

model-00001-of-00003.safetensors:   0%|          | 0.00/3.72G [00:00<?, ?B/s]

model-00002-of-00003.safetensors:   0%|          | 0.00/4.99G [00:00<?, ?B/s]

model-00003-of-00003.safetensors:   0%|          | 0.00/1.15G [00:00<?, ?B/s]

ValueError: Some modules are dispatched on the CPU or the disk. Make sure you have enough GPU RAM to fit the quantized model. If you want to dispatch the model on the CPU or the disk while keeping these modules in 32-bit, you need to set `llm_int8_enable_fp32_cpu_offload=True` and pass a custom `device_map` to `from_pretrained`. Check https://huggingface.co/docs/transformers/main/en/main_classes/quantization#offload-between-cpu-and-gpu for more details. 

In [5]:
from transformers import TextStreamer
def inference(messages, max_new_tokens=128):
  return model.generate(
      **tokenizer.apply_chat_template(
          messages,
          add_generation_prompt = True,
          tokenize = True,
          return_dict = True,
          return_tensors = "pt"
      ).to("cuda"),
    max_new_tokens = max_new_tokens,
    temperature = 1.0,
    top_p = 0.95,
    top_k = 64,
   # streamer = TextStreamer(tokenizer,skip_prompt=True)
  )


In [6]:
messages = [
    {
        "role":"user",
        "content":[{"type":"text",
                    "text":"hi"
                  }]
    }
]

Data Prep

In [82]:
from unsloth.chat_templates import get_chat_template
tokenizer = get_chat_template(
    tokenizer,
    chat_template = "gemma-3"
)

In [11]:
from datasets import load_dataset

dataset = load_dataset("mlabonne/FineTome-100k",split = "train[:3000]")

README.md:   0%|          | 0.00/982 [00:00<?, ?B/s]

data/train-00000-of-00001.parquet:   0%|          | 0.00/117M [00:00<?, ?B/s]

Generating train split:   0%|          | 0/100000 [00:00<?, ? examples/s]

In [14]:
dataset

Dataset({
    features: ['conversations', 'source', 'score'],
    num_rows: 3000
})

In [36]:
from unsloth.chat_templates import standardize_data_formats
def formatting_prompts_func(examples):
  print("Examples:", examples) # Added print statement
  convos = examples["conversations"]
  texts = [tokenizer.apply_chat_template(convo,tokenize = False, add_generation_prompt = False).removeprefix("<bos>") for convo in convos]
  return {"texts":texts,}

dataset_2 = dataset_2.map(formatting_prompts_func,batched = True)

Map:   0%|          | 0/3000 [00:00<?, ? examples/s]

Examples: {'conversations': [[{'content': 'Explain what boolean operators are, what they do, and provide examples of how they can be used in programming. Additionally, describe the concept of operator precedence and provide examples of how it affects the evaluation of boolean expressions. Discuss the difference between short-circuit evaluation and normal evaluation in boolean expressions and demonstrate their usage in code. \n\nFurthermore, add the requirement that the code must be written in a language that does not support short-circuit evaluation natively, forcing the test taker to implement their own logic for short-circuit evaluation.\n\nFinally, delve into the concept of truthiness and falsiness in programming languages, explaining how it affects the evaluation of boolean expressions. Add the constraint that the test taker must write code that handles cases where truthiness and falsiness are implemented differently across different programming languages.', 'role': 'user'}, {'cont

In [45]:
model = FastModel.get_peft_model(
    model,
    r = 8,
    lora_alpha = 8,
    lora_dropout = 0,
    bias = "none",
    random_state = 3407
)

Unsloth: Making `model.base_model.model.model.language_model` require gradients


In [46]:
from trl import SFTTrainer, SFTConfig

trainer = SFTTrainer(
    model = model,
    tokenizer = tokenizer,
    train_dataset = dataset_2,
    eval_dataset = None,
    args = SFTConfig(
        dataset_text_field = "texts",
        per_device_train_batch_size = 1,
        gradient_accumulation_steps = 4,
        warmup_steps = 5,
        max_steps = 60,
        learning_rate =2e-4,
        logging_steps = 1,
        optim = "adamw_8bit",
        weight_decay = 0.01,
        lr_scheduler_type = "linear",
        seed = 3407,
        report_to = "none"
    ),
   # formatting_func=formatting_prompts_func,
)

In [47]:
from unsloth.chat_templates import train_on_responses_only

trainer = train_on_responses_only(
    trainer,
    instruction_part = "<start_of_turn>user\n",
    response_part = "<start_of_turn>model\n"
)

Map (num_proc=2):   0%|          | 0/3000 [00:00<?, ? examples/s]

In [50]:
import torch._dynamo
torch._dynamo.config.cache_size_limit = 128
trainer_stats = trainer.train()

==((====))==  Unsloth - 2x faster free finetuning | Num GPUs used = 1
   \\   /|    Num examples = 3,000 | Num Epochs = 1 | Total steps = 60
O^O/ \_/ \    Batch size per device = 1 | Gradient accumulation steps = 4
\        /    Data Parallel GPUs = 1 | Total batch size (1 x 4 x 1) = 4
 "-____-"     Trainable parameters = 19,210,240 of 7,869,188,432 (0.24% trained)


Unsloth: Will smartly offload gradients to save VRAM!


In [83]:
messages = [
    {
        "role":"user",
        "content":[
            {
                "type":"text",
                "text":"continue the sequence 1,1,2,3,5,8,",
            }

          ]
    }
]


inputs = tokenizer.apply_chat_template(
    messages,
    add_generation_prompt = True,
    return_tensors = "pt",
    tokenize = True,
    return_dict = True
).to("cuda")
outputs = model.generate(**inputs, max_new_tokens = 64,temperature = 1.0)
